In [1]:
def define_searchspace(trial):
    model_type = trial.suggest_categorical('model', ['fsr_model.LSTM', 'fsr_model.CNN_LSTM', 'fsr_model.ANN'])
    if model_type == 'fsr_model.LSTM':
        trial.suggest_categorical('model_args/hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/num_layer', 1, 8)
    elif model_type == 'fsr_model.CNN_LSTM':
        trial.suggest_categorical('model_args/cnn_hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_categorical('model_args/lstm_hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/cnn_num_layer', 1, 8)
        trial.suggest_int('model_args/lstm_num_layer', 1, 8)
    elif model_type == 'fsr_model.ANN':
        trial.suggest_categorical('model_args/hidden_size', [8, 16, 32, 64, 128])
        trial.suggest_int('model_args/num_layer', 1, 8)
    trial.suggest_categorical('criterion', ['torch.nn.MSELoss'])
    trial.suggest_categorical('optimizer', [
        'torch.optim.Adam',
        'torch.optim.NAdam',
        'torch.optim.Adagrad',
        'torch.optim.RAdam',
        'torch.optim.SGD',
    ])
    trial.suggest_float('optimizer_args/lr', 1e-5, 1e-1, log=True)
    trial.suggest_categorical('scaler', [
        'sklearn.preprocessing.StandardScaler',
        'sklearn.preprocessing.MinMaxScaler',
        'sklearn.preprocessing.RobustScaler',
    ])

In [2]:
import ray.tune
import ray.air
import ray.air.integrations.wandb
import ray.tune.schedulers
import datasource
from trainable import Trainable
import ray.tune.search
import ray.tune.search.optuna

tuner = ray.tune.Tuner(
    trainable=ray.tune.with_resources(
        ray.tune.with_parameters(Trainable, data=datasource.get_data()),
        {'cpu':2},
    ),
    tune_config=ray.tune.TuneConfig(
        num_samples=-1,
        scheduler=ray.tune.schedulers.ASHAScheduler(
            max_t=100,
            grace_period=1,
            reduction_factor=2,
            brackets=1,
            metric='rmse',
            mode='min',
        ),
        search_alg=ray.tune.search.optuna.OptunaSearch(
            space=define_searchspace,
            metric='rmse',
            mode='min',
        ),
    ), 
    run_config=ray.air.RunConfig(
        # callbacks=[
        #     ray.air.integrations.wandb.WandbLoggerCallback(project='FSR-prediction'),
        # ],
        checkpoint_config=ray.air.CheckpointConfig(
            num_to_keep=3,
            checkpoint_score_attribute='rmse',
            checkpoint_score_order='min',
            checkpoint_frequency=5,
            checkpoint_at_end=True,
        ), 
    ),
) 
results = tuner.fit()

[I 2023-07-02 05:45:02,257] A new study created in memory with name: optuna
2023-07-02 05:45:04,399	INFO worker.py:1627 -- Started a local Ray instance. View the dashboard at 127.0.0.1:8265 
2023-07-02 05:45:05,679	INFO tune.py:226 -- Initializing Ray automatically. For cluster usage or custom Ray initialization, call `ray.init(...)` before `Tuner(...)`.


(Trainable pid=62087) tensor([[ 1.1350e-01,  3.3895e-01,  2.6895e-01, -1.1435e-01,  5.3234e-01,
(Trainable pid=62087)           1.0435e+00],
(Trainable pid=62087)         [ 1.6173e-01,  3.9626e-01,  3.0414e-01, -1.8258e-01,  5.3234e-01,
(Trainable pid=62087)           1.0080e+00],
(Trainable pid=62087)         [ 2.4212e-01,  4.8796e-01,  3.3932e-01, -2.2807e-01,  5.3234e-01,
(Trainable pid=62087)           9.7245e-01],
(Trainable pid=62087)         [ 3.3858e-01,  6.1405e-01,  3.8624e-01, -2.8114e-01,  5.3234e-01,
(Trainable pid=62087)           9.7245e-01],
(Trainable pid=62087)         [ 4.2700e-01,  7.5160e-01,  4.2143e-01, -3.1905e-01,  5.0681e-01,
(Trainable pid=62087)           9.7245e-01],
(Trainable pid=62087)         [ 5.0738e-01,  9.0061e-01,  4.9180e-01, -3.4937e-01,  4.8129e-01,
(Trainable pid=62087)           9.7245e-01],
(Trainable pid=62087)         [ 5.8776e-01,  1.0382e+00,  5.8563e-01, -3.8728e-01,  5.3234e-01,
(Trainable pid=62087)           9.7245e-01],
(Trainable pi

(Trainable pid=62087) tensor([[-0.4126, -0.5459, -0.5483,  0.4195, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.4088, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3743, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3549, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3625, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3452, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3119, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3151, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3420, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3646, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.5483,  0.3786, -0.3318, -0.3239],
(Trainable pid=62087)         [-0.4126, -0.5459, -0.54

(Trainable pid=62456)         [ 0.0000,  0.0000, -0.5893,  2.1494,  0.0000, 74.0000]]) tensor([[ 0.0000, -0.0708, -0.1137,  1.3892,  0.0000,  0.4000], [repeated 47x across cluster]
(Trainable pid=62456)    5.87008417e+00  9.79211926e-01]] [repeated 37968x across cluster]
(Trainable pid=62456)      6.8354553 ] [repeated 40x across cluster]
(Trainable pid=62456)         ..., [repeated 71x across cluster]
(Trainable pid=62456)  ... [repeated 36x across cluster]
(Trainable pid=62456)  [ 2.37289958e+01 -4.38481653e+01  3.07451894e+01  6.37927104e+02 [repeated 29057x across cluster]
(Trainable pid=62456)           2.4000e+00]]) [[ 5.46543915e+02  4.99646560e+02  2.44233036e+02 -2.76980626e+02 [repeated 78x across cluster]
(Trainable pid=62456) tensor([[ 4.0385e-01, -7.0755e-02, -1.1373e-01,  4.5317e-01,  0.0000e+00, [repeated 146x across cluster]
